In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf

In [2]:
train = pd.read_csv('train.csv')
train_id = train['Id']
train.drop("Id", axis = 1, inplace = True)
train.head()

MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0          60       RL         65.0     8450   Pave   NaN      Reg   
1          20       RL         80.0     9600   Pave   NaN      Reg   
2          60       RL         68.0    11250   Pave   NaN      IR1   
3          70       RL         60.0     9550   Pave   NaN      IR1   
4          60       RL         84.0    14260   Pave   NaN      IR1   

  LandContour Utilities LotConfig    ...     PoolArea PoolQC Fence  \
0         Lvl    AllPub    Inside    ...            0    NaN   NaN   
1         Lvl    AllPub       FR2    ...            0    NaN   NaN   
2         Lvl    AllPub    Inside    ...            0    NaN   NaN   
3         Lvl    AllPub    Corner    ...            0    NaN   NaN   
4         Lvl    AllPub       FR2    ...            0    NaN   NaN   

  MiscFeature MiscVal MoSold  YrSold  SaleType  SaleCondition  SalePrice  
0         NaN       0      2    2008        WD         Normal     208500  
1         NaN       0      5    2007        WD         Normal     181500  
2         NaN       0      9    2008        WD         Normal     223500  
3         NaN       0      2    2006        WD        Abnorml     140000  
4         NaN       0     12    2008        WD         Normal     250000  

[5 rows x 80 columns]

In [3]:
test = pd.read_csv('test.csv')
test_id = test['Id']
test.drop("Id", axis = 1, inplace = True)
test.head()

MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0          20       RH         80.0    11622   Pave   NaN      Reg   
1          20       RL         81.0    14267   Pave   NaN      IR1   
2          60       RL         74.0    13830   Pave   NaN      IR1   
3          60       RL         78.0     9978   Pave   NaN      IR1   
4         120       RL         43.0     5005   Pave   NaN      IR1   

  LandContour Utilities LotConfig      ...       ScreenPorch PoolArea PoolQC  \
0         Lvl    AllPub    Inside      ...               120        0    NaN   
1         Lvl    AllPub    Corner      ...                 0        0    NaN   
2         Lvl    AllPub    Inside      ...                 0        0    NaN   
3         Lvl    AllPub    Inside      ...                 0        0    NaN   
4         HLS    AllPub    Inside      ...               144        0    NaN   

   Fence MiscFeature MiscVal  MoSold  YrSold  SaleType  SaleCondition  
0  MnPrv         NaN       0       6    2010        WD         Normal  
1    NaN        Gar2   12500       6    2010        WD         Normal  
2  MnPrv         NaN       0       3    2010        WD         Normal  
3    NaN         NaN       0       6    2010        WD         Normal  
4    NaN         NaN       0       1    2010        WD         Normal  

[5 rows x 79 columns]

In [4]:
train = train.drop(train[(train['GrLivArea'] > 4000) & (train['SalePrice'] < 300000)].index)
train["SalePrice"] = np.log1p(train["SalePrice"])

In [5]:
x_train = train.shape[0]
x_test = test.shape[0]
y_train = train.SalePrice.values
alldata = pd.concat((train, test)).reset_index(drop=True)
alldata.drop(['SalePrice'], axis=1, inplace=True)
print("all_data size is : {}".format(alldata.shape))

all_data size is : (2917, 79)


In [6]:
alldata["PoolQC"] = alldata["PoolQC"].fillna("None")
alldata["MiscFeature"] = alldata["MiscFeature"].fillna("None")
alldata["Alley"] = alldata["Alley"].fillna("None")
alldata["Fence"] = alldata["Fence"].fillna("None")
alldata["FireplaceQu"] = alldata["FireplaceQu"].fillna("None")
alldata["LotFrontage"] = alldata.groupby("Neighborhood")["LotFrontage"].transform(lambda x: x.fillna(x.median()))
for col in ('GarageType', 'GarageFinish', 'GarageQual', 'GarageCond'):
    alldata[col] = alldata[col].fillna('None')
for col in ('GarageYrBlt', 'GarageArea', 'GarageCars'):
    alldata[col] = alldata[col].fillna(0)
for col in ('BsmtFinSF1', 'BsmtFinSF2', 'BsmtUnfSF','TotalBsmtSF', 'BsmtFullBath', 'BsmtHalfBath'):
    alldata[col] = alldata[col].fillna(0)
for col in ('BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2'):
    alldata[col] = alldata[col].fillna('None')
alldata["MasVnrType"] = alldata["MasVnrType"].fillna("None")
alldata["MasVnrArea"] = alldata["MasVnrArea"].fillna(0)
alldata['MSZoning'] = alldata['MSZoning'].fillna(alldata['MSZoning'].mode()[0])
alldata = alldata.drop(['Utilities'], axis=1)
alldata["Functional"] = alldata["Functional"].fillna("Typ")
alldata['Electrical'] = alldata['Electrical'].fillna(alldata['Electrical'].mode()[0])
alldata['KitchenQual'] = alldata['KitchenQual'].fillna(alldata['KitchenQual'].mode()[0])
alldata['Exterior1st'] = alldata['Exterior1st'].fillna(alldata['Exterior1st'].mode()[0])
alldata['Exterior2nd'] = alldata['Exterior2nd'].fillna(alldata['Exterior2nd'].mode()[0])
alldata['SaleType'] = alldata['SaleType'].fillna(alldata['SaleType'].mode()[0])
alldata['MSSubClass'] = alldata['MSSubClass'].fillna("None")
alldata['MSSubClass'] = alldata['MSSubClass'].apply(str)
alldata['OverallCond'] = alldata['OverallCond'].astype(str)
alldata['YrSold'] = alldata['YrSold'].astype(str)
alldata['MoSold'] = alldata['MoSold'].astype(str)

In [7]:
alldata['TotalSF'] = alldata['TotalBsmtSF'] + alldata['1stFlrSF'] + alldata['2ndFlrSF']

In [8]:
from scipy.stats import skew

numeric_feats = alldata.dtypes[alldata.dtypes != "object"].index
skewed_feats = alldata[numeric_feats].apply(lambda x: skew(x.dropna())).sort_values(ascending=False)
skewness = pd.DataFrame({'Skew' :skewed_feats})

skewness = skewness[abs(skewness) > 0.75]
from scipy.special import boxcox1p
skewed_features = skewness.index
lam = 0.15
for feat in skewed_features:
    alldata[feat] = boxcox1p(alldata[feat], lam)

In [9]:
all_data = pd.get_dummies(alldata)
print(all_data.shape)

(2917, 338)


In [10]:
train = all_data[:y_train.shape[0]].values
test = all_data[y_train.shape[0]:].values

In [11]:
def rmsle(y, y_pred):
    return np.sqrt(mean_squared_error(y, y_pred))

In [25]:
tf.reset_default_graph()
X = tf.placeholder(tf.float32, (None, all_data.shape[1]))
Y = tf.placeholder(tf.float32, (None, 1))

# linear regression
w = tf.Variable(tf.zeros([all_data.shape[1], 1]))
b = tf.Variable(tf.zeros([1]))
logits = tf.matmul(X, w) + b

# RMSE because the competition using this one
cost = tf.sqrt(tf.reduce_mean(tf.square(logits  - Y)))

# i suggest you decay every certain epoch
optimizer = tf.train.RMSPropOptimizer(0.0001).minimize(cost)

sess = tf.InteractiveSession()
sess.run(tf.global_variables_initializer())

for i in range(200000):
    total = 0
    
    # 5 folds
    for x in range(0, (train.shape[0] // 291) * 291, 291):
        y_reshape = y_train[x: x + 291].reshape([291, 1])
        loss, _ = sess.run([cost, optimizer], feed_dict = {X: train[x: x + 291, :], Y: y_reshape})
        total += np.mean(loss)
    print('loss: ', total / (train.shape[0] // 291))
        

loss:  12.0296438217
loss:  12.0280824661
loss:  12.0268463135
loss:  12.0257011414
loss:  12.024593544
loss:  12.0235017776
loss:  12.0224151611
loss:  12.0213300705
loss:  12.0202440262
loss:  12.0191556931
loss:  12.0180641174
loss:  12.0169706345
loss:  12.0158746719
loss:  12.0147764206
loss:  12.0136764526
loss:  12.0125759125
loss:  12.0114740372
loss:  12.0103713989
loss:  12.0092679977
loss:  12.0081645966
loss:  12.0070606232
loss:  12.0059568405
loss:  12.0048526764
loss:  12.0037485123
loss:  12.0026445389
loss:  12.0015399933
loss:  12.0004358292
loss:  11.9993314743
loss:  11.9982273102
loss:  11.9971227646
loss:  11.9960184097
loss:  11.9949142456
loss:  11.9938097
loss:  11.9927051544
loss:  11.9916009903
loss:  11.9904968262
loss:  11.9893920898
loss:  11.9882879257
loss:  11.9871835709
loss:  11.9860794067
loss:  11.9849750519
loss:  11.983870697
loss:  11.9827659607
loss:  11.9816617966
loss:  11.9805574417
loss:  11.9794528961
loss:  11.978348732
loss:  11.977244377

loss:  11.5554168701
loss:  11.5543125153
loss:  11.5532083511
loss:  11.5521043777
loss:  11.5510002136
loss:  11.549895668
loss:  11.5487918854
loss:  11.5476877213
loss:  11.5465835571
loss:  11.545479393
loss:  11.5443750381
loss:  11.5432710648
loss:  11.5421667099
loss:  11.5410627365
loss:  11.5399583817
loss:  11.5388544083
loss:  11.5377502441
loss:  11.5366458893
loss:  11.5355419159
loss:  11.5344379425
loss:  11.5333333969
loss:  11.5322292328
loss:  11.5311254501
loss:  11.5300210953
loss:  11.5289173126
loss:  11.5278131485
loss:  11.5267086029
loss:  11.5256044388
loss:  11.5245004654
loss:  11.5233966827
loss:  11.5222921371
loss:  11.521187973
loss:  11.5200839996
loss:  11.5189798355
loss:  11.5178756714
loss:  11.5167715073
loss:  11.5156675339
loss:  11.514563179
loss:  11.5134592056
loss:  11.51235466
loss:  11.5112508774
loss:  11.5101467133
loss:  11.5090427399
loss:  11.5079380035
loss:  11.5068340302
loss:  11.5057300568
loss:  11.5046258926
loss:  11.503521728

loss:  11.1159999847
loss:  11.1148956299
loss:  11.1137918472
loss:  11.1126876831
loss:  11.1115837097
loss:  11.1104801178
loss:  11.1093757629
loss:  11.1082719803
loss:  11.1071680069
loss:  11.1060640335
loss:  11.1049598694
loss:  11.1038560867
loss:  11.1027521133
loss:  11.10164814
loss:  11.1005443573
loss:  11.0994405746
loss:  11.0983364105
loss:  11.0972324371
loss:  11.096128273
loss:  11.0950244904
loss:  11.093920517
loss:  11.0928165436
loss:  11.0917125702
loss:  11.0906085968
loss:  11.0895048141
loss:  11.0884008408
loss:  11.0872968674
loss:  11.086192894
loss:  11.0850889206
loss:  11.0839851379
loss:  11.0828811646
loss:  11.0817773819
loss:  11.080673027
loss:  11.0795694351
loss:  11.078465271
loss:  11.0773611069
loss:  11.0762571335
loss:  11.0751531601
loss:  11.0740493774
loss:  11.0729454041
loss:  11.0718414307
loss:  11.070737648
loss:  11.0696336746
loss:  11.0685295105
loss:  11.0674255371
loss:  11.0663217545
loss:  11.0652179718
loss:  11.0641138077


loss:  10.6380327225
loss:  10.6369291306
loss:  10.6358249664
loss:  10.634721756
loss:  10.6336177826
loss:  10.6325138092
loss:  10.6314102173
loss:  10.6303066254
loss:  10.6292032242
loss:  10.6280988693
loss:  10.6269954681
loss:  10.6258918762
loss:  10.6247879028
loss:  10.6236843109
loss:  10.6225805283
loss:  10.6214769363
loss:  10.6203731537
loss:  10.619269371
loss:  10.6181657791
loss:  10.6170623779
loss:  10.6159585953
loss:  10.6148548126
loss:  10.6137506485
loss:  10.612647438
loss:  10.6115434647
loss:  10.6104400635
loss:  10.6093360901
loss:  10.6082324982
loss:  10.6071287155
loss:  10.6060253143
loss:  10.6049215317
loss:  10.603817749
loss:  10.6027139664
loss:  10.601609993
loss:  10.6005064011
loss:  10.5994029999
loss:  10.5982990265
loss:  10.5971952438
loss:  10.5960916519
loss:  10.59498806
loss:  10.5938840866
loss:  10.592780304
loss:  10.5916769028
loss:  10.5905733109
loss:  10.5894695282
loss:  10.588366127
loss:  10.5872619629
loss:  10.5861581802
l

loss:  10.156876564
loss:  10.1557733536
loss:  10.1546699524
loss:  10.1535663605
loss:  10.15246315
loss:  10.1513597488
loss:  10.1502561569
loss:  10.1491529465
loss:  10.1480495453
loss:  10.1469459534
loss:  10.1458427429
loss:  10.1447393417
loss:  10.1436357498
loss:  10.1425321579
loss:  10.1414291382
loss:  10.1403255463
loss:  10.1392221451
loss:  10.1381183624
loss:  10.1370153427
loss:  10.1359121323
loss:  10.1348083496
loss:  10.1337049484
loss:  10.1326019287
loss:  10.1314983368
loss:  10.1303951263
loss:  10.1292917252
loss:  10.128188324
loss:  10.1270849228
loss:  10.1259815216
loss:  10.1248781204
loss:  10.1237743378
loss:  10.1226711273
loss:  10.1215679169
loss:  10.120464325
loss:  10.1193611145
loss:  10.1182580948
loss:  10.1171545029
loss:  10.1160507202
loss:  10.1149477005
loss:  10.1138442993
loss:  10.1127407074
loss:  10.1116371155
loss:  10.1105342865
loss:  10.1094306946
loss:  10.1083272934
loss:  10.1072237015
loss:  10.106120491
loss:  10.105017089

...

loss:  0.0903159692883
loss:  0.0903159618378
loss:  0.0903159722686
loss:  0.0903159245849
loss:  0.0903159305453
loss:  0.0903159245849
loss:  0.0903159216046
loss:  0.0903159290552
loss:  0.0903159186244
loss:  0.0903159081936
loss:  0.0903158977628
loss:  0.0903158679605
loss:  0.0903158292174
loss:  0.0903158396482
loss:  0.0903158649802
loss:  0.0903158456087
loss:  0.090315836668
loss:  0.0903158500791
loss:  0.0903158470988
loss:  0.0903158396482
loss:  0.0903158485889
loss:  0.0903158262372
loss:  0.0903157860041
loss:  0.0903158143163
loss:  0.0903157636523
loss:  0.0903158023953
loss:  0.0903157666326
loss:  0.0903157383204
loss:  0.0903157770634
loss:  0.0903157636523
loss:  0.0903157189488
loss:  0.090315708518
loss:  0.0903156906366
loss:  0.0903156653047
loss:  0.0903156816959
loss:  0.0903156802058
loss:  0.0903156861663
loss:  0.0903156772256
loss:  0.0903156623244
loss:  0.0903156369925
loss:  0.0903156593442
loss:  0.0903156250715
loss:  0.0903156369925
loss:  0.0903

loss:  0.0903128743172
loss:  0.0903128892183
loss:  0.0903128728271
loss:  0.0903128892183
loss:  0.0903128549457
loss:  0.0903128325939
loss:  0.090312859416
loss:  0.0903127998114
loss:  0.0903128132224
loss:  0.090312820673
loss:  0.0903128236532
loss:  0.0903127759695
loss:  0.0903128087521
loss:  0.0903128162026
loss:  0.0903127744794
loss:  0.0903127610683
loss:  0.0903127402067
loss:  0.0903127685189
loss:  0.0903127670288
loss:  0.0903127402067
loss:  0.0903127163649
loss:  0.0903127491474
loss:  0.0903127238154
loss:  0.0903127416968
loss:  0.0903126999736
loss:  0.0903126895428
loss:  0.090312731266
loss:  0.0903127014637
loss:  0.0903126582503
loss:  0.0903126716614
loss:  0.0903126969934
loss:  0.09031265378
loss:  0.0903126120567
loss:  0.0903126180172
loss:  0.0903126105666
loss:  0.0903125911951
loss:  0.0903125867248
loss:  0.0903125956655
loss:  0.090312603116
loss:  0.0903125941753
loss:  0.0903126060963
loss:  0.0903125911951
loss:  0.0903125867248
loss:  0.09031255

loss:  0.0903099447489
loss:  0.0903099402785
loss:  0.0903099492192
loss:  0.0903099343181
loss:  0.0903099134564
loss:  0.0903099343181
loss:  0.0903098851442
loss:  0.090309882164
loss:  0.0903098717332
loss:  0.0903098404408
loss:  0.0903098419309
loss:  0.0903098389506
loss:  0.0903098642826
loss:  0.090309818089
loss:  0.0903098270297
loss:  0.0903098359704
loss:  0.0903098404408
loss:  0.0903098329902
loss:  0.0903097957373
loss:  0.0903098091483
loss:  0.0903097644448
loss:  0.0903097748756
loss:  0.0903097555041
loss:  0.0903097748756
loss:  0.0903097704053
loss:  0.0903097376227
loss:  0.0903097599745
loss:  0.0903097510338
loss:  0.0903097599745
loss:  0.0903097167611
loss:  0.0903097450733
loss:  0.0903097063303
loss:  0.0903096869588
loss:  0.09030970186
loss:  0.0903096988797
loss:  0.0903096705675
loss:  0.0903096497059
loss:  0.0903096720576
loss:  0.0903096199036
loss:  0.0903096362948
loss:  0.0903096243739
loss:  0.0903096273541
loss:  0.0903096362948
loss:  0.090309

loss:  0.0903070092201
loss:  0.0903069838881
loss:  0.0903069749475
loss:  0.0903069764376
loss:  0.0903069749475
loss:  0.0903069809079
loss:  0.0903069406748
loss:  0.0903069466352
loss:  0.0903069570661
loss:  0.0903069287539
loss:  0.0903069227934
loss:  0.0903069376945
loss:  0.0903069213033
loss:  0.0903069078922
loss:  0.0903068885207
loss:  0.0903068885207
loss:  0.0903068765998
loss:  0.0903068616986
loss:  0.090306854248
loss:  0.0903068929911
loss:  0.090306854248
loss:  0.0903068616986
loss:  0.0903068631887
loss:  0.0903068065643
loss:  0.0903067976236
loss:  0.0903068199754
loss:  0.0903068110347
loss:  0.0903067886829
loss:  0.0903067976236
loss:  0.090306802094
loss:  0.0903067916632
loss:  0.0903067931533
loss:  0.0903067678213
loss:  0.0903067857027
loss:  0.090306776762
loss:  0.0903067559004
loss:  0.0903067097068
loss:  0.0903066933155
loss:  0.0903066962957
loss:  0.0903067097068
loss:  0.0903066948056
loss:  0.0903066679835
loss:  0.0903066620231
loss:  0.090306

loss:  0.090303888917
loss:  0.0903038665652
loss:  0.090303876996
loss:  0.0903038606048
loss:  0.0903038695455
loss:  0.0903038337827
loss:  0.0903038442135
loss:  0.0903038099408
loss:  0.0903038114309
loss:  0.090303812921
loss:  0.090303824842
loss:  0.0903037935495
loss:  0.0903037920594
loss:  0.0903038159013
loss:  0.0903037905693
loss:  0.0903037682176
loss:  0.0903037533164
loss:  0.0903037458658
loss:  0.0903037369251
loss:  0.0903037384152
loss:  0.0903037369251
loss:  0.0903037324548
loss:  0.090303722024
loss:  0.0903037056327
loss:  0.0903036952019
loss:  0.0903036653996
loss:  0.0903036609292
loss:  0.0903036564589
loss:  0.0903036922216
loss:  0.090303657949
loss:  0.0903036341071
loss:  0.0903036534786
loss:  0.0903036385775
loss:  0.0903036266565
loss:  0.0903036281466
loss:  0.0903036206961
loss:  0.0903035730124
loss:  0.0903035774827
loss:  0.0903035923839
loss:  0.0903035894036
loss:  0.0903035610914
loss:  0.0903035283089
loss:  0.0903035476804
loss:  0.09030357

In [26]:
output = sess.run(logits, feed_dict = {X: test})
output = output.reshape([-1])
output = np.expm1(output)
sub = pd.DataFrame()
sub['Id'] = test_id
sub['SalePrice'] = output
sub.to_csv('submission2.csv',index = False)

# Accuracy between 0.12 - 0.19